In [1]:
import pickle
import numpy as np
import cvxpy as cp
import matplotlib.pyplot as plt
import copy

In [2]:
teams = ['BKN', 'MIL', 'GSW', 'LAL', 'IND', 'CHA', 'CHI', 'DET',
          'WAS', 'TOR', 'BOS', 'NYK', 'CLE', 'MEM', 'PHI', 'NOP',
          'HOU','MIN', 'ORL', 'SAS', 'OKC', 'UTA', 'SAC', 'POR',
          'DEN', 'PHX', 'DAL', 'ATL', 'MIA', 'LAC']

In [3]:
file_name = '../team-profiles/profiles.pkl'
with open(file_name, 'rb') as file:
    # Use pickle.load() to read the list from the file
    team_profiles = pickle.load(file)

In [4]:
def print_params(params):
    M_, N_, E_, R_ = params['M'], params['N'], params['E'], params['R']

    print(f'M = {np.round(M_, 2)}')
    print(f'N = {np.round(N_, 2)}')
    print(f'E = {np.round(E_, 2)}')
    for p in players:
        print(f'R[{p}] = {np.round(R_[p], 2)}')

In [5]:
N_players = 5
n_components = 3 # num of hidden states
n_features = 3 # num of observed states
O_symbols = [0, 1, 2] # under-, avg-, over- performance
H_symbols = [0, 1, 2] # corresponding mental states
initial_dist = np.array([0, 1, 0])

In [6]:
def cond(player, h1, h2, t, M_, N_, R_): # P(H_t^player = h1 | H_{t-1}^player = h2, O_{t-1})
    # Requires M_, N_, R_, Os
    v = [N_[h2][h1]]
    for teammate in players:
        v.append(M_[Os[teammate][t-1]][h1])
            
    v = np.array(v)
    return np.dot(R_[player], v)  

In [7]:
def calculate_forward(M_, N_, E_, R_):
    alpha = {p: [] for p in players}
    alpha_help = {p: [] for p in players}
    
    # Initialize forward parameters
    for p in players:
        alpha_help[p].append(initial_dist)
    for p in players:
        arr = np.array([E_[h][Os[p][0]] * alpha_help[p][0][h] for h in H_symbols])
        arr /= np.sum(arr)
        alpha[p].append(arr)

    # Compute forward parameters (bottom-up)
    for p in players:
        for t in range(1, T):
            arr = [sum([cond(p, h, h_, t, M_, N_, R_) * alpha[p][t-1][h_] for h_ in H_symbols]) for h in H_symbols]
            arr = np.array(arr)
            alpha_help[p].append(arr)
            
            arr = [E_[h][Os[p][t]] * alpha_help[p][t][h] for h in H_symbols]
            arr = np.array(arr)
            arr /= np.sum(arr)
            alpha[p].append(arr)
            
    return alpha, alpha_help

In [8]:
def rename_keys(original_dict, key_mapping):
    new_dict = {}
    for old_key, new_key in key_mapping.items():
        if old_key in original_dict:
            new_dict[new_key] = original_dict[old_key]
    return new_dict

In [9]:
def likelihood(params): # Calculate log P(O) (given the model parameters)
    M, N, E, R = params['M'], params['N'], params['E'], params['R']
    
    # Caluclate forward parameters
    alpha, alpha_help = calculate_forward(M, N, E, R)
    obj = 0
    for p in players:
        for t in range(T):
            if isinstance(E, dict):
                obj += -np.log(sum([E[p][h][Os[p][t]] * alpha_help[p][t][h] for h in H_symbols])) # Pr(O_t^i | O_{1:t-1})
            else:
                obj += -np.log(sum([E[h][Os[p][t]] * alpha_help[p][t][h] for h in H_symbols])) # Pr(O_t^i | O_{1:t-1})

    return obj

def likelihood_test(params_dict):
    total_params = len(params_dict)
    # Given a list of model parameters returns the model parameters that achieve the highest likelihood
    val_opt = 1e+100
    i = 1
    for key in params_dict:
        params = params_dict[key]
        params['R'] = rename_keys(params['R'], key_mapping)
        val = likelihood(params)
        print(f'{i} / {total_params}, val = {np.round(val, 2)}')
        i += 1
        if val < val_opt:
            val_opt = val
            params_opt = params
        
    return params_opt

In [10]:
Os_teams = {team: dict() for team in teams}
for team in teams:
    with open(f'../team-data/observations/{team}_observations.pickle', 'rb') as file:
            observations = pickle.load(file)
    
    k = list(observations.keys())[0]
    players = list(observations[k].keys())
    
    Os_teams[team] = {p: [] for p in players}
    for game_id in observations:
        game_stats = observations[game_id]
        for p in players:
            Os_teams[team][p].extend(game_stats[p])

In [11]:
for team in teams:
    print(f'Team = {team}')
    try:
        players = list(Os_teams[team].keys())[:N_players]
        i = 1
        key_mapping = dict()
        for p in players:
            key_mapping[f'player{i}'] = players[i-1]
            i += 1

        Os = Os_teams[team]
        T = len(Os[players[0]])
        profiles = copy.deepcopy(team_profiles)
        team_params = likelihood_test(profiles)

        # Open the file in binary write mode
        with open(f'./profiles/{team}_profile.pkl', 'wb') as file:
            pickle.dump(team_params, file)
            
    except:
        print(f'Error for team {team}')

# print(f'=== Params for {team} ===')
# print_params(team_params)

Team = BKN
1 / 5667, val = 1055.91
2 / 5667, val = 1094.26
3 / 5667, val = 1286.36
4 / 5667, val = 1153.83
5 / 5667, val = 1280.62
6 / 5667, val = 1151.22
7 / 5667, val = 1293.67
8 / 5667, val = 1155.82
9 / 5667, val = 1213.94
10 / 5667, val = 1265.39
11 / 5667, val = 1135.39
12 / 5667, val = 1186.83
13 / 5667, val = 1135.56
14 / 5667, val = 1215.14
15 / 5667, val = 1090.34
16 / 5667, val = 1169.92
17 / 5667, val = 1251.58
18 / 5667, val = 1055.91
19 / 5667, val = 1094.26
20 / 5667, val = 1196.2
21 / 5667, val = 1408.65
22 / 5667, val = 1195.8
23 / 5667, val = 1195.22
24 / 5667, val = 1354.32
25 / 5667, val = 1120.37
26 / 5667, val = 1233.37
27 / 5667, val = 1120.41
28 / 5667, val = 1120.39
29 / 5667, val = 1205.71
30 / 5667, val = 1196.2
31 / 5667, val = 1408.65
32 / 5667, val = 1195.8
33 / 5667, val = 1195.22
34 / 5667, val = 1354.32
35 / 5667, val = 1120.37
36 / 5667, val = 1233.37
37 / 5667, val = 1120.41
38 / 5667, val = 1120.39
39 / 5667, val = 1205.71
40 / 5667, val = 1196.2
41 

321 / 5667, val = 1156.05
322 / 5667, val = 1165.16
323 / 5667, val = 1230.78
324 / 5667, val = 1231.28
325 / 5667, val = 1152.37
326 / 5667, val = 1237.01
327 / 5667, val = 1238.02
328 / 5667, val = 1282.12
329 / 5667, val = 1182.2
330 / 5667, val = 1222.53
331 / 5667, val = 1223.47
332 / 5667, val = 1236.41
333 / 5667, val = 1280.63
334 / 5667, val = 1281.27
335 / 5667, val = 1221.39
336 / 5667, val = 1124.18
337 / 5667, val = 1124.81
338 / 5667, val = 1164.54
339 / 5667, val = 1075.96
340 / 5667, val = 1110.19
341 / 5667, val = 1111.04
342 / 5667, val = 1123.86
343 / 5667, val = 1164.71
344 / 5667, val = 1164.44
345 / 5667, val = 1110.06
346 / 5667, val = 1194.85
347 / 5667, val = 1194.59
348 / 5667, val = 1214.22
349 / 5667, val = 1156.58
350 / 5667, val = 1178.84
351 / 5667, val = 1178.46
352 / 5667, val = 1195.11
353 / 5667, val = 1214.56
354 / 5667, val = 1214.42
355 / 5667, val = 1179.08
356 / 5667, val = 1254.8
357 / 5667, val = 1115.71
358 / 5667, val = 1141.14
359 / 5667, va

1540 / 5667, val = 1052.63
1541 / 5667, val = 1055.29
1542 / 5667, val = 1107.55
1543 / 5667, val = 1125.62
1544 / 5667, val = 1126.29
1545 / 5667, val = 1199.02
1546 / 5667, val = 1053.87
1547 / 5667, val = 1108.56
1548 / 5667, val = 1108.65
1549 / 5667, val = 1135.7
1550 / 5667, val = 1034.36
1551 / 5667, val = 1034.48
1552 / 5667, val = 1109.29
1553 / 5667, val = 1136.31
1554 / 5667, val = 1137.23
1555 / 5667, val = 1205.98
1556 / 5667, val = 1036.0
1557 / 5667, val = 1109.59
1558 / 5667, val = 1110.46
1559 / 5667, val = 1123.21
1560 / 5667, val = 1127.12
1561 / 5667, val = 1173.17
1562 / 5667, val = 1087.76
1563 / 5667, val = 1113.41
1564 / 5667, val = 1117.49
1565 / 5667, val = 1124.47
1566 / 5667, val = 1171.77
1567 / 5667, val = 1173.19
1568 / 5667, val = 1112.88
1569 / 5667, val = 1117.76
1570 / 5667, val = 1121.05
1571 / 5667, val = 1170.59
1572 / 5667, val = 1058.07
1573 / 5667, val = 1100.52
1574 / 5667, val = 1103.15
1575 / 5667, val = 1119.28
1576 / 5667, val = 1167.77
157

1850 / 5667, val = 1094.66
1851 / 5667, val = 1093.81
1852 / 5667, val = 1299.96
1853 / 5667, val = 1113.33
1854 / 5667, val = 1267.14
1855 / 5667, val = 1114.07
1856 / 5667, val = 1113.73
1857 / 5667, val = 1223.65
1858 / 5667, val = 1185.74
1859 / 5667, val = 1137.59
1860 / 5667, val = 1143.42
1861 / 5667, val = 1168.55
1862 / 5667, val = 1185.84
1863 / 5667, val = 1186.18
1864 / 5667, val = 1260.22
1865 / 5667, val = 1137.03
1866 / 5667, val = 1167.07
1867 / 5667, val = 1168.12
1868 / 5667, val = 1195.32
1869 / 5667, val = 1081.88
1870 / 5667, val = 1082.75
1871 / 5667, val = 1160.94
1872 / 5667, val = 1195.24
1873 / 5667, val = 1195.75
1874 / 5667, val = 1283.09
1875 / 5667, val = 1081.68
1876 / 5667, val = 1160.0
1877 / 5667, val = 1159.57
1878 / 5667, val = 1176.3
1879 / 5667, val = 1140.2
1880 / 5667, val = 1143.25
1881 / 5667, val = 1165.05
1882 / 5667, val = 1176.9
1883 / 5667, val = 1176.57
1884 / 5667, val = 1223.64
1885 / 5667, val = 1140.56
1886 / 5667, val = 1165.33
1887 

2158 / 5667, val = 1123.66
2159 / 5667, val = 1123.1
2160 / 5667, val = 1152.72
2161 / 5667, val = 1187.76
2162 / 5667, val = 1187.43
2163 / 5667, val = 1123.71
2164 / 5667, val = 1107.34
2165 / 5667, val = 1202.26
2166 / 5667, val = 1155.22
2167 / 5667, val = 1092.52
2168 / 5667, val = 1434.21
2169 / 5667, val = 1101.29
2170 / 5667, val = 1098.17
2171 / 5667, val = 1361.13
2172 / 5667, val = 1104.45
2173 / 5667, val = 1272.55
2174 / 5667, val = 1105.2
2175 / 5667, val = 1105.91
2176 / 5667, val = 1230.41
2177 / 5667, val = 1092.52
2178 / 5667, val = 1434.21
2179 / 5667, val = 1101.29
2180 / 5667, val = 1098.17
2181 / 5667, val = 1361.13
2182 / 5667, val = 1104.45
2183 / 5667, val = 1272.55
2184 / 5667, val = 1105.2
2185 / 5667, val = 1105.91
2186 / 5667, val = 1230.41
2187 / 5667, val = 1092.52
2188 / 5667, val = 1434.21
2189 / 5667, val = 1101.29
2190 / 5667, val = 1098.17
2191 / 5667, val = 1361.13
2192 / 5667, val = 1104.45
2193 / 5667, val = 1272.55
2194 / 5667, val = 1105.2
2195 

...

4141 / 5667, val = 1655.11
4142 / 5667, val = 1697.06
4143 / 5667, val = 1618.98
4144 / 5667, val = 1687.97
4145 / 5667, val = 1630.68
4146 / 5667, val = 1694.96
4147 / 5667, val = 1624.63
4148 / 5667, val = 1676.7
4149 / 5667, val = 1685.09
4150 / 5667, val = 1648.94
4151 / 5667, val = 1686.95
4152 / 5667, val = 1689.48
4153 / 5667, val = 1677.61
4154 / 5667, val = 1694.33
4155 / 5667, val = 1689.83
4156 / 5667, val = 1706.75
4157 / 5667, val = 1686.87
4158 / 5667, val = 1732.57
4159 / 5667, val = 1640.55
4160 / 5667, val = 1706.65
4161 / 5667, val = 1666.78
4162 / 5667, val = 1720.05
4163 / 5667, val = 1639.97
4164 / 5667, val = 1668.82
4165 / 5667, val = 1772.12
4166 / 5667, val = 1656.91
4167 / 5667, val = 1658.92
4168 / 5667, val = 1731.48
4169 / 5667, val = 1683.4
4170 / 5667, val = 1720.54
4171 / 5667, val = 1705.4
4172 / 5667, val = 1734.0
4173 / 5667, val = 1689.21
4174 / 5667, val = 1711.96
4175 / 5667, val = 1758.32
4176 / 5667, val = 1708.22
4177 / 5667, val = 1714.41
4178 

4449 / 5667, val = 2139.96
4450 / 5667, val = 1701.58
4451 / 5667, val = 2083.67
4452 / 5667, val = 1705.94
4453 / 5667, val = 1774.21
4454 / 5667, val = 1791.25
4455 / 5667, val = 1637.12
4456 / 5667, val = 1786.29
4457 / 5667, val = 1823.06
4458 / 5667, val = 1883.88
4459 / 5667, val = 1717.66
4460 / 5667, val = 1826.43
4461 / 5667, val = 1955.48
4462 / 5667, val = 1742.79
4463 / 5667, val = 1939.96
4464 / 5667, val = 1772.05
4465 / 5667, val = 1936.11
4466 / 5667, val = 1739.35
4467 / 5667, val = 1813.12
4468 / 5667, val = 1855.83
4469 / 5667, val = 1730.0
4470 / 5667, val = 1825.81
4471 / 5667, val = 1899.66
4472 / 5667, val = 1769.5
4473 / 5667, val = 1898.98
4474 / 5667, val = 1799.86
4475 / 5667, val = 1909.19
4476 / 5667, val = 1775.69
4477 / 5667, val = 1721.9
4478 / 5667, val = 1741.93
4479 / 5667, val = 1652.73
4480 / 5667, val = 1723.19
4481 / 5667, val = 1788.25
4482 / 5667, val = 1673.04
4483 / 5667, val = 1781.97
4484 / 5667, val = 1681.51
4485 / 5667, val = 1780.94
4486

4754 / 5667, val = 1679.48
4755 / 5667, val = 1698.19
4756 / 5667, val = 1682.71
4757 / 5667, val = 1703.83
4758 / 5667, val = 1685.74
4759 / 5667, val = 1700.04
4760 / 5667, val = 1713.91
4761 / 5667, val = 1698.8
4762 / 5667, val = 1705.66
4763 / 5667, val = 1694.22
4764 / 5667, val = 1607.82
4765 / 5667, val = 1601.3
4766 / 5667, val = 1782.82
4767 / 5667, val = 1873.57
4768 / 5667, val = 1917.3
4769 / 5667, val = 1675.85
4770 / 5667, val = 1884.54
4771 / 5667, val = 1644.95
4772 / 5667, val = 1688.75
4773 / 5667, val = 1705.6
4774 / 5667, val = 1591.65
4775 / 5667, val = 1695.9
4776 / 5667, val = 1782.82
4777 / 5667, val = 1873.57
4778 / 5667, val = 1917.3
4779 / 5667, val = 1675.85
4780 / 5667, val = 1884.54
4781 / 5667, val = 1644.95
4782 / 5667, val = 1688.75
4783 / 5667, val = 1705.6
4784 / 5667, val = 1591.65
4785 / 5667, val = 1695.9
4786 / 5667, val = 1782.82
4787 / 5667, val = 1873.57
4788 / 5667, val = 1917.3
4789 / 5667, val = 1675.85
4790 / 5667, val = 1884.54
4791 / 566

5064 / 5667, val = 1726.55
5065 / 5667, val = 1712.25
5066 / 5667, val = 1732.07
5067 / 5667, val = 1708.78
5068 / 5667, val = 1695.42
5069 / 5667, val = 1767.37
5070 / 5667, val = 1707.4
5071 / 5667, val = 1700.58
5072 / 5667, val = 1741.24
5073 / 5667, val = 1716.8
5074 / 5667, val = 1744.71
5075 / 5667, val = 1729.84
5076 / 5667, val = 1751.26
5077 / 5667, val = 1732.25
5078 / 5667, val = 1732.97
5079 / 5667, val = 1769.46
5080 / 5667, val = 1739.17
5081 / 5667, val = 1743.08
5082 / 5667, val = 1694.87
5083 / 5667, val = 1669.97
5084 / 5667, val = 1689.45
5085 / 5667, val = 1679.77
5086 / 5667, val = 1695.97
5087 / 5667, val = 1674.82
5088 / 5667, val = 1678.49
5089 / 5667, val = 1718.22
5090 / 5667, val = 1674.45
5091 / 5667, val = 1673.1
5092 / 5667, val = 1707.11
5093 / 5667, val = 1693.22
5094 / 5667, val = 1707.61
5095 / 5667, val = 1697.36
5096 / 5667, val = 1715.16
5097 / 5667, val = 1698.28
5098 / 5667, val = 1716.03
5099 / 5667, val = 1720.32
5100 / 5667, val = 1706.22
5101

5369 / 5667, val = 1901.41
5370 / 5667, val = 1748.87
5371 / 5667, val = 1800.66
5372 / 5667, val = 1833.29
5373 / 5667, val = 1738.83
5374 / 5667, val = 1812.06
5375 / 5667, val = 1876.45
5376 / 5667, val = 1776.1
5377 / 5667, val = 1886.69
5378 / 5667, val = 1789.95
5379 / 5667, val = 1872.57
5380 / 5667, val = 1778.03
5381 / 5667, val = 1729.35
5382 / 5667, val = 1747.72
5383 / 5667, val = 1663.79
5384 / 5667, val = 1728.72
5385 / 5667, val = 1792.09
5386 / 5667, val = 1682.15
5387 / 5667, val = 1785.56
5388 / 5667, val = 1688.95
5389 / 5667, val = 1782.86
5390 / 5667, val = 1681.79
5391 / 5667, val = 1711.96
5392 / 5667, val = 1713.87
5393 / 5667, val = 1665.07
5394 / 5667, val = 1722.56
5395 / 5667, val = 1732.42
5396 / 5667, val = 1699.75
5397 / 5667, val = 1740.99
5398 / 5667, val = 1709.32
5399 / 5667, val = 1754.02
5400 / 5667, val = 1710.95
5401 / 5667, val = 1845.46
5402 / 5667, val = 1727.69
5403 / 5667, val = 1817.8
5404 / 5667, val = 1753.07
5405 / 5667, val = 1819.83
540